# **Handwritten text recognition**

Authors:

*   Daniel Kohl, AMSM
*   Matěj Trödler, AMSM



First of all, install all neccesary packages

In [22]:
!pip install Pillow
!pip install lightning
!pip install opencv-python
!pip install torchvision
!pip install Wandb

In [26]:
import os
import torch
import torch.nn as nn
import lightning.pytorch as pl
from lightning.pytorch.loggers import CSVLogger, WandbLogger
import torch.nn.functional as F

from torch.utils.data import DataLoader, Dataset
from torchvision import transforms
from torchvision.transforms import ToTensor, Resize, ColorJitter, RandomRotation, \
    RandomAdjustSharpness, RandomAutocontrast, AutoAugment

import matplotlib.pyplot as plt
import pandas as pd
from tqdm import tqdm
from zipfile import ZipFile
from urllib.request import urlopen
from io import BytesIO
from PIL import Image
import tarfile


import wandb

#Download data
This function downloads data from a given path and extractc it into new folder *Datasets*. Data consists of folder *words* with many subfolders with images. Then it also contains text file *words.txt* with images file path and the annotated label.

In [24]:
def download_and_unzip(url, extract_to='Datasets', chunk_size=1024*1024):
    http_response = urlopen(url)

    data = b''
    iterations = http_response.length // chunk_size + 1
    for _ in tqdm(range(iterations)):
        data += http_response.read(chunk_size)

    zipfile = ZipFile(BytesIO(data))
    zipfile.extractall(path=extract_to)

Now we extract data into form which we would like to work with. We create an array dataset with path of the image and a label of it. Then we construct a set vocab with all used characters. Note that it contains all capital letters, small-letters and also punctuation marks as ?!,.- etc. Finally, we would like to know the length of the longest word in dataset. As will be seen, it will be used in the DataModule. There are also images which are demaged, so we have to skip them and dont work with them.

In [27]:
dataset_path = os.path.join('Datasets', 'IAM_Words')
if not os.path.exists(dataset_path):
    download_and_unzip('https://git.io/J0fjL', extract_to='Datasets')

    file = tarfile.open(os.path.join(dataset_path, "words.tgz"))
    file.extractall(os.path.join(dataset_path, "words"))


dataset, vocab, max_len = [], set(), 0

# Preprocess the dataset by the specific IAM_Words dataset file structure
words = open(os.path.join(dataset_path, "words.txt"), "r").readlines()
for line in tqdm(words):
    if line.startswith("#"):
        continue

    line_split = line.split(" ")
    if line_split[1] == "err":
        continue

    folder1 = line_split[0][:3] # extract the folder name
    folder2 = "-".join(line_split[0].split("-")[:2]) # extract the sub-folder name
    file_name = line_split[0] + ".png" # extract the file name
    label = line_split[-1].rstrip('\n') # the label, last element of row, remove the \n at the end

    # the relative path to the image file
    rel_path = os.path.join(dataset_path, "words", folder1, folder2, file_name)
    try:
        # Attempt to open the image
        image = Image.open(rel_path).convert("RGB")
    except (Image.UnidentifiedImageError, OSError) as e:
        print(f"Error opening image: {rel_path}, {e}")
        continue

    # append path and the label to dataset
    dataset.append([rel_path, label])

    # append label to vocab
    vocab.update(list(label))

    # length of the longest word
    max_len = max(max_len, len(label))

  0%|          | 419/115338 [00:00<00:36, 3109.65it/s]

Error opening image: Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-00.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-00.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-01.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-01.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-02.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-02.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-03.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-03.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-04.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-04.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-000u/a01-000u-00-05.png, [Errno 2] No such file or directory: 'Datasets

  1%|▏         | 1601/115338 [00:00<00:27, 4118.94it/s]

Error opening image: Datasets/IAM_Words/words/a01/a01-011/a01-011-03-01.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-011/a01-011-03-01.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-011/a01-011-03-02.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-011/a01-011-03-02.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-011/a01-011-03-03.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-011/a01-011-03-03.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-011/a01-011-03-04.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-011/a01-011-03-04.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-011/a01-011-03-05.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a01-011/a01-011-03-05.png'
Error opening image: Datasets/IAM_Words/words/a01/a01-011/a01-011-03-06.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/a01/a

  2%|▏         | 2345/115338 [00:00<00:26, 4339.38it/s]

...

Error opening image: Datasets/IAM_Words/words/p02/p02-135/p02-135-03-06.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/p02/p02-135/p02-135-03-06.png'
Error opening image: Datasets/IAM_Words/words/p02/p02-135/p02-135-04-00.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/p02/p02-135/p02-135-04-00.png'
Error opening image: Datasets/IAM_Words/words/p02/p02-135/p02-135-04-01.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/p02/p02-135/p02-135-04-01.png'
Error opening image: Datasets/IAM_Words/words/p02/p02-135/p02-135-04-02.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/p02/p02-135/p02-135-04-02.png'
Error opening image: Datasets/IAM_Words/words/p02/p02-135/p02-135-04-03.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/p02/p02-135/p02-135-04-03.png'
Error opening image: Datasets/IAM_Words/words/p02/p02-135/p02-135-04-04.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/p02/p

 98%|█████████▊| 113187/115338 [00:09<00:00, 13506.25it/s]

Error opening image: Datasets/IAM_Words/words/r03/r03-030/r03-030-04-05.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r03/r03-030/r03-030-04-05.png'
Error opening image: Datasets/IAM_Words/words/r03/r03-030/r03-030-04-06.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r03/r03-030/r03-030-04-06.png'
Error opening image: Datasets/IAM_Words/words/r03/r03-030/r03-030-04-07.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r03/r03-030/r03-030-04-07.png'
Error opening image: Datasets/IAM_Words/words/r03/r03-030/r03-030-05-00.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r03/r03-030/r03-030-05-00.png'
Error opening image: Datasets/IAM_Words/words/r03/r03-030/r03-030-05-01.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r03/r03-030/r03-030-05-01.png'
Error opening image: Datasets/IAM_Words/words/r03/r03-030/r03-030-05-02.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r03/r

100%|██████████| 115338/115338 [00:09<00:00, 11636.82it/s]


Error opening image: Datasets/IAM_Words/words/r06/r06-121/r06-121-07-06.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r06/r06-121/r06-121-07-06.png'
Error opening image: Datasets/IAM_Words/words/r06/r06-121/r06-121-07-07.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r06/r06-121/r06-121-07-07.png'
Error opening image: Datasets/IAM_Words/words/r06/r06-121/r06-121-08-00.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r06/r06-121/r06-121-08-00.png'
Error opening image: Datasets/IAM_Words/words/r06/r06-121/r06-121-08-01.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r06/r06-121/r06-121-08-01.png'
Error opening image: Datasets/IAM_Words/words/r06/r06-121/r06-121-08-02.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r06/r06-121/r06-121-08-02.png'
Error opening image: Datasets/IAM_Words/words/r06/r06-121/r06-121-08-03.png, [Errno 2] No such file or directory: 'Datasets/IAM_Words/words/r06/

We would like to work with sorted vocab. In the following script, in NN, we will have to work with numbers instead of strings, so we will convert words into arrays as follows: we will transfer each character into numbers that the numbers denote position of that letter in the vocab. There is an example:

In [ ]:
vocab = "".join(sorted(vocab))
print(vocab)

In [ ]:
example = ['peter', 'america', ',', 'you']

indices_array = np.array([vocab.index(l) for word in example for l in word if l in vocab])
print(indices_array)

#DataModule
Now let's prepare a DataModule for our neural network. At first, we will define a class Dataset, which will return an image and its label from the dataset array. It will also split the data into training and validation data.

In [ ]:
class IAMWordsDataset(Dataset):
    def __init__(self, dataset, vocab, max_len, split="train", train_val_split=0.9):
        self.dataset = dataset
        self.vocab = vocab
        self.max_len = max_len
        self.split = split
        self.train_val_split = train_val_split

        # maybe it should be assigned own vocab and max_len to train/val dataset, but idk
        if self.split == "train":
            self.dataset = self.dataset[:int(len(self.dataset) * self.train_val_split)]
        elif self.split == "val":
            self.dataset = self.dataset[int(len(self.dataset) * self.train_val_split):]

    def __len__(self):
        return len(self.dataset)

    def __getitem__(self, idx):
        image_path, label = self.dataset[idx]
        image = Image.open(image_path).convert("RGB")
#------------------------------------------------------------------------------
        #print("Hello World")
        #torch.cuda.synchronize(print(f"Loaded image size: {image.size}"))
#------------------------------------------------------------------------------
        return image, label

Now let's construct a DataModule. At first, we will need to resize images into same size and also convert into tensor. But before that, in training dataloader, we have to use many augmentors for better accuracy for out net. At first, brightness israndomly adjusted within the range of $[-0.5, 0.5]$. We also apply random rotation within the range of 30°. We also randomly adjust sharpness and constrast. Labels are converted to integer tensors, with each character represented by its index in the vocabulary. Then padded labels are created using the max_len to ensure a consistent length for batch processing. Finally, transformed images and padded labels are returned as the collated batch.

In [ ]:
class TextRecognitionDataModule(pl.LightningDataModule):
    def __init__(self, dataset, vocab, max_len, batch_size=64):
        super().__init__()
        self.batch_size = batch_size
        self.dataset = dataset
        self.vocab = vocab
        self.max_len = max_len

    def setup(self, stage=None):
        self.train_dataloader()
        self.val_dataloader()


    def train_dataloader(self):
        self.train_dataset = IAMWordsDataset(self.dataset, self.vocab, self.max_len, split="train")
        print("Train Dataloader called")
        return DataLoader(self.train_dataset, batch_size=self.batch_size, shuffle=True,
                          collate_fn=self.train_collate, num_workers=0)

    def val_dataloader(self):
        self.val_dataset = IAMWordsDataset(self.dataset, self.vocab, self.max_len, split="val")
        print("Validation Dataloader called")
        return DataLoader(self.val_dataset, batch_size=self.batch_size,
                          collate_fn=self.val_collate, num_workers=0)

    # ensure the same size of images and convert it to tensor
    def train_collate(self, batch):
        images, labels = zip(*batch)
        #print(labels)

        transform = transforms.Compose([
            Resize((128, 32)),
            ColorJitter(brightness=0.5),
            RandomRotation(degrees=30),
            #RandomAffine(degrees=0, shear=10),
            #RandomAffine(degrees=0, translate=(0.1, 0.1)),
            #RandomAffine(degrees=0, scale=(0.8, 1.2)),
            RandomAdjustSharpness(sharpness_factor=2),
            RandomAutocontrast(),
            #RandomErasing(),
            AutoAugment(),
            ToTensor()])

        images = [transform(image) for image in images]

        # Convert labels to integer tensors

        converted_labels = []
        for label in labels:
            converted_label = [self.vocab.index(l) for l in label if l in self.vocab]
            converted_labels.append(torch.tensor(converted_label, dtype=torch.long))

        #print(converted_labels)

        # Pad the labels to the same length for batch processing
        padded_labels = torch.nn.utils.rnn.pad_sequence(converted_labels,
                                                        batch_first=True,
                                                        padding_value=0)
        return torch.stack(images), padded_labels

    def val_collate(self, batch):
        images, labels = zip(*batch)
        #print(labels)

        #--------------------------------------------------------------------
        # Print the shape of images before processing
        #for img in images:
            #print(f"Original image size: {img.size}")
        #--------------------------------------------------------------------

        # Resize all images to a consistent size (e.g., 128x32)
        transform = transforms.Compose([
            Resize((128, 32)),
            ToTensor()])

        images = [transform(image) for image in images]

        # Convert labels to integer tensors

        converted_labels = []
        for label in labels:
            converted_label = [self.vocab.index(l) for l in label if l in self.vocab]
            converted_labels.append(torch.tensor(converted_label, dtype=torch.long))

        #print(converted_labels)

        # Pad the labels to the same length for batch processing
        padded_labels = torch.nn.utils.rnn.pad_sequence(converted_labels,
                                                        batch_first=True,
                                                        padding_value=0)
        return torch.stack(images), padded_labels

#Model
Now let's define our model. At first we will add a choice which activation layer can be used, there are options as ReLU or LeakyReLU.

In [ ]:
def activation_layer(activation: str="relu", alpha: float=0.1, inplace: bool=True):
    """ Activation layer wrapper for LeakyReLU and ReLU activation functions

    Args:
        activation: str, activation function name (default: 'relu')
        alpha: float (LeakyReLU activation function parameter)

    Returns:
        torch.Tensor: activation layer
    """
    if activation == "relu":
        return nn.ReLU(inplace=inplace)

    elif activation == "leaky_relu":
        return nn.LeakyReLU(negative_slope=alpha, inplace=inplace)


class ConvBlock(nn.Module):
    """ Convolutional block with batch normalization
    """
    def __init__(self, in_channels: int, out_channels: int, kernel_size: int, stride: int, padding: int):
        super(ConvBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels, out_channels, kernel_size=kernel_size, stride=stride, padding=padding)
        self.bn = nn.BatchNorm2d(out_channels)

    def forward(self, x: torch.Tensor):
        return self.bn(self.conv(x))


class ResidualBlock(nn.Module):
    def __init__(self, in_channels, out_channels, skip_conv=True, stride=1, dropout=0.2, activation="leaky_relu"):
        super(ResidualBlock, self).__init__()
        self.convb1 = ConvBlock(in_channels, out_channels, kernel_size=3, stride=stride, padding=1)
        self.act1 = activation_layer(activation)

        self.convb2 = ConvBlock(out_channels, out_channels, kernel_size=3, stride=1, padding=1)

        self.dropout = nn.Dropout(p=dropout)

        self.shortcut = None
        if skip_conv:
            if stride != 1 or in_channels != out_channels:
                self.shortcut = nn.Conv2d(in_channels, out_channels, kernel_size=1, stride=stride)

        self.act2 = activation_layer(activation)

    def forward(self, x):
        skip = x

        out = self.act1(self.convb1(x))
        out = self.convb2(out)

        if self.shortcut is not None:
            out += self.shortcut(skip)

        out = self.act2(out)
        out = self.dropout(out)

        return out

#CNN model

In [ ]:
class CNNmodel(pl.LightningModule):
    def __init__(self, pad_val, num_chars: int, activation: str="leaky_relu", dropout: float=0.2):
        super(CNNmodel, self).__init__()

        self.pad_val = pad_val

        self.rb1 = ResidualBlock(3, 16, skip_conv=True, stride=1, activation=activation, dropout=dropout)
        self.rb2 = ResidualBlock(16, 16, skip_conv=True, stride=2, activation=activation, dropout=dropout)
        self.rb3 = ResidualBlock(16, 16, skip_conv=False, stride=1, activation=activation, dropout=dropout)
        self.rb4 = ResidualBlock(16, 32, skip_conv=True, stride=2, activation=activation, dropout=dropout)
        self.rb5 = ResidualBlock(32, 32, skip_conv=False, stride=1, activation=activation, dropout=dropout)
        self.rb6 = ResidualBlock(32, 64, skip_conv=True, stride=2, activation=activation, dropout=dropout)
        self.rb7 = ResidualBlock(64, 64, skip_conv=True, stride=1, activation=activation, dropout=dropout)
        self.rb8 = ResidualBlock(64, 64, skip_conv=False, stride=1, activation=activation, dropout=dropout)
        self.rb9 = ResidualBlock(64, 64, skip_conv=False, stride=1, activation=activation, dropout=dropout)

        self.lstm = nn.LSTM(64, 128, bidirectional=True, num_layers=1, batch_first=True)
        self.lstm_dropout = nn.Dropout(p=dropout)

        self.output = nn.Linear(256, num_chars + 1)

    def forward(self, images: torch.Tensor) -> torch.Tensor:
        images_float = images / 255.0
        #images_float = images_float.permute(0, 3, 1, 2)

        #print(f"Shape after initial processing: {images_float.shape}")

#------------------------------------------------------------------------------
        x = self.rb1(images_float)
        #print(f"After rb1 Shape: {x.shape}")
        x = self.rb2(x)
        #print(f"After rb2 Shape: {x.shape}")
        x = self.rb3(x)
        #print(f"After rb3 Shape: {x.shape}")
        x = self.rb4(x)
        #print(f"After rb4 Shape: {x.shape}")
        x = self.rb5(x)
        #print(f"After rb5 Shape: {x.shape}")
        x = self.rb6(x)
        #print(f"After rb6 Shape: {x.shape}")
        x = self.rb7(x)
        #print(f"After rb7 Shape: {x.shape}")
        x = self.rb8(x)
        #print(f"After rb8 Shape: {x.shape}")
        x = self.rb9(x)
        #print(f"After rb9 Shape: {x.shape}")

        x = x.reshape(x.size(0), -1, x.size(1))
        #print(f"After Reshape Shape: {x.shape}")

        x, _ = self.lstm(x)
        x = self.lstm_dropout(x)
        #print(f"After LSTM Shape: {x.shape}")

        x = self.output(x)
        x = F.log_softmax(x, 2)
        #print('X from soft_max:', x)
        #print(f"Final Output Shape: {x.shape}")
#------------------------------------------------------------------------------

        return x

    def training_step(self, batch, batch_idx):
        images, targets = batch

        outputs = self(images)

        target_lengths = torch.sum(targets != self.pad_val, dim=1)

        targets_unpadded = targets[targets != self.pad_val].view(-1)

        outputs = outputs.permute(1, 0, 2)  # (sequence_length, batch_size, num_classes)
        outputs_lengths = torch.full(size=(outputs.size(1),), fill_value=outputs.size(0), dtype=torch.long)

        #print('Input lenghts tr', len(outputs_lengths))
        loss = F.ctc_loss(outputs, targets_unpadded, outputs_lengths, target_lengths, blank = self.pad_val)
        self.log('train_loss', loss, on_step=True, on_epoch=True, prog_bar=True, logger=True)
        return loss

    def validation_step(self, batch, batch_idx):
        images, targets = batch

        outputs = self(images)

        target_lengths = torch.sum(targets != self.pad_val, dim=1)

        targets_unpadded = targets[targets != self.pad_val].view(-1)

        outputs = outputs.permute(1, 0, 2)  # (sequence_length, batch_size, num_classes)
        outputs_lengths = torch.full(size=(outputs.size(1),), fill_value=outputs.size(0), dtype=torch.long)

        #print('Input lenghts val', len(outputs_lengths))
        loss = F.ctc_loss(outputs, targets_unpadded, outputs_lengths, target_lengths, blank = self.pad_val)
        self.log('val_loss', loss, on_step=True, on_epoch=True, prog_bar=True, logger=True)
        return loss

    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=1e-6)
        return optimizer

In [ ]:
print(torch.cuda.is_available())

#Train model

In [ ]:
# Initialize the model and data module
data_module = TextRecognitionDataModule(dataset, vocab, max_len)
model = CNNmodel(pad_val = 0, num_chars=len(vocab))
'''len(data_module.train_dataset.vocab)'''

# Prepare the data module for training
data_module.setup('train')

#------------------------------------------------------------------------------
# Test DataLoader

print("Testing DataLoader...")
#------------------------------------------------------------------------------

# Get the number of available GPUs, else use CPU
ngpus = torch.cuda.device_count() if torch.cuda.is_available() else 1

logger = CSVLogger("logs", name="TextRecognition")

# Train and Validate the model
trainer = pl.Trainer(logger=CSVLogger("logs", name="TextRecognition"), devices=ngpus, accelerator="gpu" if ngpus > 0 else None, max_epochs=2)
trainer.fit(model, data_module)

In [ ]:
log_dir = 'version_0'

def plot_csv_losses(df_cleaned):
    fig = plt.figure(figsize=(10, 4))
    plt.plot(df_cleaned['epoch'], df_cleaned['train_loss_epoch'], label='Training Loss', c='b')
    plt.plot(df_cleaned['epoch'], df_cleaned['val_loss_epoch'], label='Validation Loss', c='r')
    plt.yscale('log')
    plt.xlabel('Epochs')
    plt.ylabel('Loss')
    plt.legend()
    plt.tight_layout()
    plt.show()

log_file = f'/content/logs/TextRecognition/{log_dir}/metrics.csv'
df = pd.read_csv(log_file)
df_grouped = df.groupby('epoch').first().reset_index()
plot_csv_losses(df_grouped)

In [ ]:
def decode(output, blank_label=0):
    max_indices = torch.argmax(output, dim=-1)
    #print('max_indices:', max_indices)
    decoded_sequence = []
    for label in max_indices.cpu().numpy():
        if label != blank_label and (not decoded_sequence or label != decoded_sequence[-1]):
            decoded_sequence.append(label)
    print(decoded_sequence)

    return decoded_sequence

def label_to_string(label, vocab):
    strings = "".join([vocab[k] for k in label if k < len(vocab)])
    return strings

def calculate_accuracy(true_strings, pred_strings):
    correct_results = sum([1 for true, pred in zip(true_strings, pred_strings) if true == pred])
    total_results = len(true_strings)
    return correct_results, total_results

def calculate_digit_accuracy(true_strings, pred_strings, max_len):
    digit_correct = 0
    digit_total = 0

    for true, pred in zip(true_strings, pred_strings):
        for true_digit, pred_digit in zip(true, pred):
            digit_total += 1
            if true_digit == pred_digit:
                digit_correct += 1

    return digit_correct, digit_total

def correct(model, loader, vocab, blank_label=0):
    model.eval()
    device = next(model.parameters()).device

    #print('max_len:', data_module.max_len)

    correct_results = 0
    total_results = 0
    true_strings = []
    pred_strings = []
    digits_correct, digits_total = [], []

    with torch.no_grad():
        for x, y in loader:
            x, y = x.to(device), y.to(device)
            y_hat = model(x)

            #print('y_hat:', y_hat)
            #print('y_shape:', y_hat.shape)

            decoded_preds = [decode(word) for word in y_hat]

            y_dec = []

            for label in y:
                decoded_sequence = []
                for i in label:
                    if i != blank_label and (not decoded_sequence or i != decoded_sequence[-1]):
                        decoded_sequence.append(i)
                y_dec.append(decoded_sequence)

            pred_strings.extend([label_to_string(pred, vocab) for pred in decoded_preds])
            true_strings.extend([label_to_string(target, vocab) for target in y_dec])

            cor_res, tot_res = calculate_accuracy(true_strings, pred_strings)
            correct_results += cor_res
            total_results += tot_res

            digit_correct, digit_total = calculate_digit_accuracy(true_strings, pred_strings, data_module.max_len)
            digits_correct.append(digit_correct)
            digits_total.append(digit_total)


    accuracy = correct_results / total_results if total_results > 0 else 0.0

    digit_correct = sum(digits_correct)
    digit_total = sum(digits_total)
    digit_accuracy = digit_correct / digit_total

    return accuracy, digit_accuracy, true_strings, pred_strings

train_accuracy, train_digit_accuracy, train_true_strings, train_pred_strings = correct(model, data_module.train_dataloader(), vocab)
print(f'Training set accuracy: {train_accuracy} correctly classified, an accuracy of {train_accuracy:.2f}%!')
print(f'Training set average CER: {train_digit_accuracy:.4f}')

val_accuracy, val_digit_accuracy, val_true_strings, val_pred_strings = correct(model, data_module.val_dataloader(), vocab)
print(f'Validation set accuracy: {val_accuracy} correctly classified, an accuracy of {val_accuracy:.2f}%!')
print(f'Validation set average CER: {val_digit_accuracy:.4f}')

for i in range(min(10, len(train_true_strings))):
    print(f'True: {train_true_strings[i]}, Predicted: {train_pred_strings[i]}')